<a href="https://colab.research.google.com/github/online6731/titanic-kaggle/blob/main/titanic.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Problem

## Titanic

https://www.kaggle.com/c/titanic/

# Environment

In [ ]:
#@title Install + Import + Config { vertical-output: true }

# Install
! pip install tpot -q
! pip install -U plotly -q
! pip install category_encoders -q
! pip3 install -U pandas-profiling[notebook] -q
! pip uninstall kaggle -y -q
! pip install kaggle -q
! pip install jupyter-dash -q

# Python
import os
import re
import sys
import warnings
from functools import partial
from IPython.display import clear_output

# Data
import numpy as np
import pandas as pd
import category_encoders as ce
from pandas_profiling import ProfileReport

# Visualization
import dash
import seaborn as sns
import missingno as msno
import plotly.express as px
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import plotly.figure_factory as ff
import dash_core_components as dcc
import dash_html_components as html
from jupyter_dash import JupyterDash
from dash.dependencies import Input, Output

# ML
import tpot
import sklearn
import tensorflow as tf
from xgboost import XGBClassifier
from sklearn.ensemble import AdaBoostClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.metrics import *
from sklearn.model_selection import train_test_split
from sklearn.model_selection import cross_validate

# Google Colab
from google.colab.output import eval_js
from google.colab.data_table import DataTable

# Config
warnings.filterwarnings("ignore")
os.environ["CUDA_VISIBLE_DEVICES"]="1"
pd.set_option('plotting.backend', 'plotly')

In [ ]:
# @title Kaggle + Data

! mkdir -p ~/.kaggle
! gdown -O ~/.kaggle/kaggle.json --id 1lyHcJc_pUI72pluLt-vWKJsl0phJDZMH --quiet
! sudo chmod 600 /root/.kaggle/kaggle.json

! kaggle competitions download -c 'titanic' -q
! unzip -qo titanic.zip

# Dataset

In [ ]:
# @title Sample

main_df = pd.read_csv('train.csv').append(pd.read_csv('test.csv'))
main_df['data'] = main_df['Survived'].map(lambda x: 'test' if np.isnan(x) else 'train')
main_df.set_index('PassengerId', inplace=True)

DataTable(main_df, num_rows_per_page=5)

In [ ]:
#@title Report { vertical-output: true }

pd.set_option('plotting.backend', 'matplotlib')

ProfileReport(main_df, dark_mode=True).to_notebook_iframe()

pd.set_option('plotting.backend', 'plotly')

Summarize dataset:   0%|          | 0/26 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
#@title Feature Eng. { vertical-output: true }

df = main_df.copy()
df['Relatives'] = df['SibSp'] + df['Parch']
df['Cabin_s']   = df['Cabin'].map(lambda x: x[0] if str(x) != 'nan' else 'nan')
df['Age']       = df['Age'].map(lambda x: df['Age'].mean() // 1 if np.isnan(x) else x // 1)
df['Name_len']  = df['Name'].map(lambda x: len(x))
df['Title']     = df['Name'].map(lambda x: re.findall('.*?, (.*?)\..*', x)[0])
df['Title']     = df['Name'].map(lambda x: x if x in df['Title'].value_counts()[:10] else 'other')
df['Fare']      = df['Fare'].map(lambda x: df['Fare'].mean() // 1 if np.isnan(x) else x // 1)
df['Embarked']  = df['Embarked'].map(lambda x: 'nan' if str(x) == 'nan' else x)

df.drop(columns=['Cabin', 'Ticket', 'Name'], inplace=True)
DataTable(df, num_rows_per_page=5)

# Model

In [ ]:
#@title Split + Encode { vertical-output: true }

test_size = 0.2 #@param {type:"slider", min:0, max:1, step:0.05}

encoder_x = ce.OrdinalEncoder()
encoder_y = ce.OrdinalEncoder()

df_train = df[df['data'] == 'train'].drop(columns=['data']).replace(np.nan, -10000)

df_train_encoded_x = encoder_x.fit_transform(df_train.drop(columns=['Survived']))
df_train_encoded_y = encoder_y.fit_transform(df_train['Survived'])

train_x, test_x, train_y, test_y = train_test_split(
    df_train_encoded_x,
    df_train_encoded_y,
    test_size=test_size)

DataTable(train_x, num_rows_per_page=5)

In [ ]:
#@title Model + Train { vertical-output: true }

main_models = {
    'xgb': XGBClassifier(eval_metric='logloss'),
    'svm': sklearn.svm.SVC(),
    'adaboost': AdaBoostClassifier(),
    'rf': RandomForestClassifier(),
    'mlp': MLPClassifier(hidden_layer_sizes=(50,50))}

models = {name:model.fit(train_x, train_y) for name,model in main_models.items()}

In [ ]:
#@title Leaderboard { vertical-output: true }

metrics = ['accuracy', 'f1', 'average_precision']

scorer = lambda model, metric: round(cross_validate(model, df_train_encoded_x, df_train_encoded_y, cv=10, scoring=metric)['test_score'].mean(), 3)

leaderboard = pd.DataFrame({metric:[scorer(model, metric) for model in models.values()] for metric in metrics},
                           index=models.keys()).sort_values('accuracy')

leaderboard.plot(kind='barh', barmode='group')
# DataTable(leaderboard)

In [ ]:
#@title Save + Submit { vertical-output: true }
Submit_Result = True #@param {type:"boolean"}

model_final = models[leaderboard.sort_values('accuracy').index[-1]]

df_test = df[df['data'] == 'test'].drop(columns=['Survived', 'data']).replace(np.nan, -10000)
df_test_encoded_x = encoder_x.fit_transform(df_test)
df_test['Survived'] = model_final.predict(df_test_encoded_x).astype('int32')
df_test.to_csv('submission.csv', columns=['Survived'])

if Submit_Result:
    ! kaggle competitions submit -c titanic -f submission.csv -m 'description'
    ! sleep 5
    ! kaggle competitions submissions -c titanic | head

# pd.read_csv('submission.csv').sample(5)

100% 2.77k/2.77k [00:05<00:00, 530B/s]
Successfully submitted to Titanic - Machine Learning from DisasterfileName        date                 description              status    publicScore  privateScore  
--------------  -------------------  -----------------------  --------  -----------  ------------  
submission.csv  2021-01-17 12:06:38  description              complete  0.75837      None          
submission.csv  2021-01-17 11:49:27  description              complete  0.74641      None          
submission.csv  2021-01-17 10:17:09  description              complete  0.76076      None          
submission.csv  2021-01-17 10:12:29  description              complete  0.76315      None          
submission.csv  2021-01-17 10:11:38  description              complete  0.76315      None          
submission.csv  2021-01-17 10:11:05  description              complete  0.76315      None          
submission.csv  2021-01-17 10:08:36  description              complete  0.75358      None      

# Report

In [ ]:
#@title Dashboard { vertical-output: true, form-width: "65%" }

app = JupyterDash(__name__)
app.title = 'Dashboard'

app.layout = html.Div([dcc.Tabs([
    
    dcc.Tab(label='Dataset', children=[
        dcc.Graph(figure=df.plot(
            kind='density_heatmap',
            x='Age', y='Survived',
            facet_col='Sex',
            facet_row='Pclass'))]),
    
    dcc.Tab(label='Analysis', children=[
        dcc.Graph(figure=df.plot(
            kind='scatter',
            x='Fare',
            y='Age'))]),
    
    dcc.Tab(label='Leaderboad', children=[
        dcc.Graph(figure=leaderboard.plot(
            kind='barh',
            barmode='group'))]),

])])

app.run_server(mode='inline')
app.run_server(mode='external')
print(eval_js('google.colab.kernel.proxyPort(8050)'))

<IPython.core.display.Javascript object>

Dash app running on:


<IPython.core.display.Javascript object>

https://7jsygo8pagc-496ff2e9c6d22116-8050-colab.googleusercontent.com/


In [ ]:
# @title temp
